In [98]:
import numpy as np
import pandas as pd
import yfinance as yf
import plotly.graph_objects as go
from scipy.stats import skew, kurtosis

In [99]:
# Scarica i dati giornalieri dell'S&P 500
sp500_data = yf.download('^GSPC', start='2010-01-01', end='2024-01-01')

[*********************100%%**********************]  1 of 1 completed


In [100]:
# Calcola i ritorni giornalieri
sp500_data['Returns'] = sp500_data['Adj Close'].pct_change()

# Rimuovi i dati NaN generati dal calcolo dei ritorni
sp500_data = sp500_data.dropna()

In [101]:
# Dividi i dati per anno
returns_by_year = {year: sp500_data.loc[str(year)]['Returns'].values for year in range(2010, 2024)}

# Trova la lunghezza minima
min_length = min(len(returns) for returns in returns_by_year.values())

# Uniforma la lunghezza di ogni anno al minimo comune
returns_by_year = {year: returns[:min_length] for year, returns in returns_by_year.items()}

In [102]:
# Funzione per interpolare i colori
def interpolate_color(color1, color2, fraction):
    return [color1[i] + (color2[i] - color1[i]) * fraction for i in range(3)]

# Funzione per convertire un colore RGB in una stringa HEX
def rgb_to_hex(color):
    return '#{:02x}{:02x}{:02x}'.format(int(color[0]), int(color[1]), int(color[2]))

# Funzione per calcolare il VaR al 97.5%
def calculate_var(data, confidence_level=0.975):
    return np.percentile(data, (1 - confidence_level) * 100)

# Colori per le distribuzioni
color_start = [255, 0, 0]  # Rosso
color_end = [0, 0, 255]    # Blu
color_base = [0, 0, 0]     # Nero semitrasparente

# Creazione dei frame per l'animazione
frames = []
years = list(range(2010, 2024))
initial_hist_data = np.histogram(returns_by_year[2010], bins=40, range=(-0.1, 0.1), density=True)

for i in range(len(years) - 1):
    for j in range(101):
        fraction = j / 100
        blended_data = (1 - fraction) * returns_by_year[years[i]] + fraction * returns_by_year[years[i + 1]]
        hist_data = np.histogram(blended_data, bins=40, range=(-0.1, 0.1), density=True)
        color = interpolate_color(color_start, color_end, i / (len(years) - 1))
        mean = np.mean(blended_data) * 100
        stddev = np.std(blended_data) * np.sqrt(252) *100
        skewness = skew(blended_data)
        kurt = kurtosis(blended_data)    
        var = calculate_var(blended_data) * 100

        frames.append(go.Frame(
            data=[
                go.Bar(x=initial_hist_data[1] * 100, y=initial_hist_data[0], marker_color=rgb_to_hex(color_base), opacity=0.2, name='Start Distribution'),
                go.Bar(x=hist_data[1] * 100, y=hist_data[0], marker_color=rgb_to_hex(color), name=f'Year {years[i]}')
            ],
            layout=go.Layout(
                title=f"S&P Daily Returns Year {years[i]}",
                title_x=0.5, 
                annotations=[
                    dict(x=0.95, y=0.95, xref='paper', yref='paper', 
                         text=f"Daily Returns Mean: {mean:.2f}%<br>Volatility: {stddev:.2f}%<br>Skewness: {skewness:.2f}<br>Kurtosis: {kurt:.2f}<br>VaR(97.5%): {var:.2f}%", 
                         showarrow=False)
                ]
            ),
            name=f'Frame {i*101 + j}'
        ))

# Aggiungere i frame per l'ultimo anno 2023
final_hist_data = np.histogram(returns_by_year[2023], bins=40, range=(-0.1, 0.1), density=True)
mean = np.mean(returns_by_year[2023]) * 100
stddev = np.std(returns_by_year[2023]) * np.sqrt(252) *100
skewness = skew(returns_by_year[2023])
kurt = kurtosis(returns_by_year[2023])
var = calculate_var(returns_by_year[2023]) * 100
frames.append(go.Frame(
    data=[
        go.Bar(x=initial_hist_data[1] * 100, y=initial_hist_data[0], marker_color=rgb_to_hex(color_base), opacity=0.2, name='Start Distribution'),
        go.Bar(x=final_hist_data[1] * 100, y=final_hist_data[0], marker_color=rgb_to_hex(color_end), name='Year 2023')
    ],
    layout=go.Layout(
        title="S&P Daily Returns Year 2023",
        title_x=0.5, 
        annotations=[
            dict(x=0.95, y=0.95, xref='paper', yref='paper', 
                 text=f"Daily Returns Mean: {mean:.2f}%<br>Volatility: {stddev:.2f}%<br>Skewness: {skewness:.2f}<br>Kurtosis: {kurt:.2f}<br>VaR(97.5%): {var:.2f}%",
                 showarrow=False)
        ]
    ),
    name='Frame Final'
))


In [103]:
# Creazione della figura iniziale
mean_initial = np.mean(returns_by_year[2010]) * 100
stddev_initial = np.std(returns_by_year[2010]) * np.sqrt(252) *100
skewness_initial = skew(returns_by_year[2010])
kurt_initial = kurtosis(returns_by_year[2010])
var_initial = np.var(returns_by_year[2010]) * 100
fig = go.Figure(
    data=[
        go.Bar(x=initial_hist_data[1] * 100, y=initial_hist_data[0], marker_color=rgb_to_hex(color_base), opacity=0.2, name='Start Distribution'),
        go.Bar(x=initial_hist_data[1] * 100, y=initial_hist_data[0], marker_color=rgb_to_hex(color_start), name='Year 2010')
    ],
    layout=go.Layout(
        xaxis=dict(range=[-10, 10], autorange=True, title='Daily Returns (%)'),
        yaxis=dict(range=[0, 50], autorange=True, title='Density'),
        title=f"S&P Daily Returns Year 2010",
        title_x=0.5, 
        annotations=[
            dict(x=0.95, y=0.95, xref='paper', yref='paper', 
                 text=f"Daily Returns Mean: {mean_initial:.2f}%<br>Volatility: {stddev_initial:.2f}%<br>Skewness: {skewness_initial:.2f}<br>Kurtosis: {kurt_initial:.2f}<br>VaR(97.5%): {var_initial:.2f}%",
                 showarrow=False)
        ],
        updatemenus=[dict(type="buttons", showactive=False,
                          buttons=[dict(label="Start",
                                        method="animate",
                                        args=[None, {"frame": {"duration": 35, "redraw": True}, "fromcurrent": True}])])]
    ),
    frames=frames
)

# Visualizzazione dell'animazione nel notebook
fig.show()
